In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
import openpyxl
import re
import os
from variableUtils import *
from Utils import *
from ClassUtils import *
from pprint import pprint
import json
from collections import defaultdict
from sklearn.ensemble import RandomForestRegressor
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
from matplotlib.patches import Rectangle
from reportlab.lib.pagesizes import letter, landscape, A4, A3
from reportlab.platypus import SimpleDocTemplate, Table, TableStyle, PageBreak, Paragraph, Spacer, Image
from reportlab.lib import colors
from matplotlib.backends.backend_pdf import PdfPages
from reportlab.platypus import Paragraph, Spacer, KeepTogether, KeepInFrame 
from reportlab.lib.styles import getSampleStyleSheet, ParagraphStyle
from reportlab.lib.units import inch
import io
from openpyxl import load_workbook
from openpyxl.styles import PatternFill
from openpyxl.formatting.rule import FormulaRule
import PIL
import ast
from adjustText import adjust_text
warnings.filterwarnings('ignore')
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
print(sns.__version__)
from datetime import datetime

# get today's date
today = datetime.now().strftime('%d-%m-%Y')
print(f"Today's date: {today}")

(841.68, 1190.8799999999999)
0.13.2
Today's date: 23-07-2025


In [35]:
# Load the ebelWeights and ebelMatrix from the saved Excel files
ebelWeightsSavePath = os.path.join('2025', 'ebelWeights.xlsx')
ebelMatrixSavePath = os.path.join('2025', 'ebelMatrix.xlsx')
ebelWeights = pd.read_excel(ebelWeightsSavePath, sheet_name=None)
ebelMatrix = pd.read_excel(ebelMatrixSavePath, sheet_name=None)
importanceWeights = {"Essential": 5, "Important": 3, "Non-essential": 1}
def getWeight(row, ebelDf):
    importance = row['Importance']
    difficulty = row['Difficulty']
    return ebelDf.loc[importance, difficulty]


for key, df in ebelWeights.items():
    # if key!= '531':
    #     continue

    df.set_index('MarkingChecklist', inplace=True)
    if 'scoreWeight' not in df.columns:
        df['scoreWeight'] = df['Importance'].map(importanceWeights)

    # ebel cutoffs
    if key not in ebelMatrix.keys():
        print(f"Key {key} not found in ebelMatrix")
        continue
    ebelDf = ebelMatrix[key].set_index('Importance')
    df['ebelWeight'] = df.apply(getWeight, axis=1, ebelDf=ebelMatrix[key].set_index('Importance'))
    ebelSum = df['ebelWeight'].sum()
    ebelCutoff = ebelSum /len(df)
    ebelWeightedSum = df['ebelWeight'] * df['scoreWeight']
    ebelWeightedSum = ebelWeightedSum.sum()
    ebelWeightedCutoff = ebelWeightedSum / df['scoreWeight'].sum()
    # if key!= '524':
        # continue
    print(f"========================\nKey: {key}")
    # display(df.head())
    print(f"EBEL Cutoff: {round(ebelCutoff,2)}")
    # print(f"EBEL Weighted Sum: {ebelWeightedSum.sum()}| {df['scoreWeight'].sum()}")
    print(f"EBEL Weighted Cutoff: {round(ebelWeightedCutoff,2)}")

Key: 521
EBEL Cutoff: 74.29
EBEL Weighted Cutoff: 74.5
Key: 522
EBEL Cutoff: 74.41
EBEL Weighted Cutoff: 74.59
Key: 523
EBEL Cutoff: 74.41
EBEL Weighted Cutoff: 74.59
Key: 524
EBEL Cutoff: 74.41
EBEL Weighted Cutoff: 74.59
Key: 532
EBEL Cutoff: 62.65
EBEL Weighted Cutoff: 65.0
Key: 533
EBEL Cutoff: 52.94
EBEL Weighted Cutoff: 54.06
Key: 534
EBEL Cutoff: 52.94
EBEL Weighted Cutoff: 54.06
Key: 577
EBEL Cutoff: 30.0
EBEL Weighted Cutoff: 30.0
Key: 577-2
EBEL Cutoff: 30.0
EBEL Weighted Cutoff: 30.0
Key: 578
EBEL Cutoff: 41.0
EBEL Weighted Cutoff: 42.37
Key: 531
EBEL Cutoff: 77.5
EBEL Weighted Cutoff: 79.91
Key: IC-BOH
EBEL Cutoff: 84.44
EBEL Weighted Cutoff: 86.97
Key: DDI-DDS
EBEL Cutoff: 70.0
EBEL Weighted Cutoff: 95.68
Key: SOR-DDS
EBEL Cutoff: 50.0
EBEL Weighted Cutoff: 91.53
Key: SOP-DDS
EBEL Cutoff: 87.5
EBEL Weighted Cutoff: 96.08
Key: MAR-31-DDS
EBEL Cutoff: 49.62
EBEL Weighted Cutoff: 50.55
Key: FS-DDS
EBEL Cutoff: 100.0
EBEL Weighted Cutoff: 100.0
Key: 011
EBEL Cutoff: 48.89
EBEL

## Json to excel

In [13]:
jsonfilepath = '2025\DDS2\dds2_v2.json'
folder, file, ext = getFolderandFileName(jsonfilepath)
with open(jsonfilepath, 'r', encoding='utf-8') as file:
    data = json.load(file)
print(json.dumps(data, indent=4, ensure_ascii=False))

{
    "success": true,
    "result": [
        {
            "assessment_id": 61,
            "student_name": "Anjali Bhatnagar",
            "student_number": 1514500,
            "datetime": "2025-07-07T00:00:00",
            "cohort": "DDS2",
            "subject": "DENT90146",
            "type": "Clinic",
            "forms": {
                "0E5Sia": {
                    "data": {
                        "student": {
                            "728-MP": {
                                "MC1": "Yes",
                                "MC2": "Yes",
                                "MC3": "No",
                                "MC4": "Yes"
                            },
                            "reflection": "44M occlusal rest seat was prepared too buccally, so demo had to do a 44OB restoration. 43L cingulum ledge rest was fine. Guide plane was fine as well. \nValuable learning opportunity for me to better assess the tooth from all angles prior to and while drilling into the too

In [14]:
# Fields to pull out from supervisor_data
supervisorMainFields = ['time_mgmt', 'entrustment', 'communication', 'professionalism', 'assessor_feedback', 
                        'clinical_incident', 'patient_complexity']

def getStudentList(listpath, cohort='BOH3'):
    listdf = pd.read_excel(listpath, keep_default_na=False, na_values=[''])
    if cohort is not None:
        listdf = listdf[listdf['Cohort'] == cohort]
    validIds = listdf['Student ID'].to_list()
    # convert to int
    validIds = [int(id) for id in validIds]
    print(f"Number of valid student IDs in {cohort}: {len(validIds)}")
    return validIds
validIds = getStudentList('2025\RE_ Student List.xlsx', cohort=None)


allEntries = []
for entry in data['result']:
    date = entry.get('date', 'Unknown Date')
    studentId = entry.get('student_number', 'Unknown ID')
    if studentId not in validIds:
        print(f"Skipping entry for student ID {studentId} as it is not in the valid list.")
        continue
    baseData = {k: v for k, v in entry.items() if not isinstance(v, dict)}
    # print(f"Base Data: {baseData}")

    # now the forms data
    forms = entry.get('forms', {})
    if not forms:
        print("No forms data found")
        continue
    for form_name, form_data in forms.items():

        data = form_data.get('data', {})
        if not data:
            print(f"No data found for form {form_name}")
            continue
        student_data = data.get('student', {})
        assessor_data = data.get('assessor', {})
        serializedFormData = {
            k: json.dumps(v) if isinstance(v, dict) else v
            for k, v in form_data.items()
        }
        serializedFormData['student_data'] = json.dumps(student_data) if isinstance(student_data, dict) else student_data
        serializedFormData['assessor_data'] = json.dumps(assessor_data) if isinstance(assessor_data, dict) else assessor_data
        row = {
            **baseData,
            'form_name': form_name,
            **serializedFormData
        }
        allEntries.append(row)
    # print(f"Row Data: {row}")
    # break

df = pd.DataFrame(allEntries)
# df.to_excel(os.path.join(folder, f"all_data_combined_v2.xlsx"), index=False)

Number of valid student IDs in None: 619
Skipping entry for student ID 1234567 as it is not in the valid list.
No forms data found
Skipping entry for student ID 1234567 as it is not in the valid list.
No forms data found
No forms data found
Skipping entry for student ID 1234567 as it is not in the valid list.
No forms data found
Skipping entry for student ID 1234567 as it is not in the valid list.


## Get scores

In [62]:
workbookpath = '2025\DDS2\\all_data_combined_v2.xlsx'
folder, file, ext = getFolderandFileName(workbookpath)
df = pd.read_excel(workbookpath)
df = df[df['datetime'] == '2025-07-18T00:00:00']
df.reset_index(inplace=True)
# display(df)
df['formDataParsed'] = df['assessor_data'].apply(json.loads)
expandedDf = pd.json_normalize(df['formDataParsed'], sep='.')
# display(expandedDf.head())
# in columns replace DDS2-MAR-31. with ''
expandedDf.columns = expandedDf.columns.str.replace('DDS2-MAR-31.', '', regex=False)
# replace .scale with ''
expandedDf.columns = expandedDf.columns.str.replace('.scale', '', regex=False)
# display(expandedDf.head())

mcCols = [col for col in expandedDf.columns if 'MC' in col and 'positioning' not in col]
print(expandedDf.columns)
colOrder = mcCols + ['positioning.MC1',	'positioning.MC2']+['time_mgmt', 'communication', 'professionalism', 'entrustment', 'reflection']
expandedDf = expandedDf[colOrder]
expandedDf = expandedDf.rename(columns={
    'time_mgmt': 'TS',
    'communication': 'CS',
    'professionalism': 'PS',
    'entrustment': 'ES',
    'reflection': 'Assessor Feedback'
})
expandedDf = expandedDf.rename(columns={
    'positioning.MC1': 'PEC_MC1',
    'positioning.MC2': 'PEC_MC2'
})
expandedDf.replace('Not Assessed', 'NA', inplace=True)
expandedDf.reset_index(inplace=True)
df = pd.concat([df, expandedDf], axis=1)
print(df.columns)
# display(df)
columns = [
    'assessment_id',
    'student_name',
    'student_number',
    'datetime',
    'cohort',
    'subject',
    'type',
    'completed'
]
columns += mcCols
columns += ['PEC_MC1', 'PEC_MC2', 'TS', 'CS', 'PS', 'ES', 'Assessor Feedback']
df = df[columns]
df = df.rename(columns={
    'assessment_id': 'Assessment ID',
    'student_name': 'Student Name',
    'student_number': 'Student ID',
    'datetime': 'Date',
    'cohort': 'Cohort',
    'subject': 'Subject',
    'type': 'Type',
    'completed': 'Completed'
})
weightPS = 0.05
weightTS = 0.025
weightES = 0.15
weightCS = 0.0
colTS = 'TS'
colES = 'ES'
colCS = 'CS'
colPS = 'PS'
weightMC = round(1 - weightPS - weightTS - weightES - weightCS, 3)
# convert all rubric columns to numeric
df[colTS] = pd.to_numeric(df[colTS], errors='coerce').astype(int)
df[colES] = pd.to_numeric(df[colES], errors='coerce').astype(int)
df[colCS] = pd.to_numeric(df[colCS], errors='coerce').astype(int)
df[colPS] = pd.to_numeric(df[colPS], errors='coerce').astype(int)

Index(['reflection', 'time_mgmt', 'MC1', 'MC2', 'MC3', 'MC4', 'MC5', 'MC6',
       'MC7', 'MC8', 'MC9', 'MC10', 'MC11', 'MC12', 'MC13', 'MC14', 'MC15',
       'MC16', 'MC17', 'MC18', 'MC19', 'MC20', 'MC21', 'MC22', 'MC23', 'MC24',
       'MC25', 'MC26', 'entrustment', 'positioning.MC1', 'positioning.MC2',
       'communication', 'professionalism'],
      dtype='object')
Index(['index', 'assessment_id', 'student_name', 'student_number', 'datetime',
       'cohort', 'subject', 'type', 'completed', 'form_name', 'data', 'role',
       'clinic', 'scales', 'version', 'checklists', 'assessor_id',
       'patient_age', 'patient_drn', 'assessor_name', 'patient_details',
       'patient_interpreter', 'submitted_by_student', 'additional_checklists',
       'submitted_by_assessor', 'student_data', 'assessor_data',
       'fta_substitute', 'teeth_quadrant_details', 'formDataParsed', 'index',
       'MC1', 'MC2', 'MC3', 'MC4', 'MC5', 'MC6', 'MC7', 'MC8', 'MC9', 'MC10',
       'MC11', 'MC12', 'MC13',

In [63]:

# get score from the ebelWeights
for i, row in df.iterrows():
    item = 'DDS2-MAR-31'
    item = 'MAR-31-DDS'
    weightDf = ebelWeights.get(item, None)
    if weightDf is None:
        print(f"Weight DataFrame for {item} not found in ebelWeights")
        continue
    # select a subset from row that is mcCols
    mcRow = row[mcCols]

    notNA = mcRow[mcRow != 'NA']
    # notNA = row
    display(notNA)
    if notNA.empty:
        print(f'Item Code: {item} has no data')
        continue
    # display(notNA.head())
    cutoff = 0
    weightedCutoff = 0
    weightedSum = 0
    denominator = 0
    # display(weightDf)
    for col in notNA.index:
        # print(cutoff, weightedCutoff, weightedSum, denominator)
        try:
            cutoff += weightDf.loc[col, 'ebelWeight']
            weightedCutoff += weightDf.loc[col, 'ebelWeight'] * weightDf.loc[col, 'scoreWeight']
            if notNA.loc[col] == 'Yes':
                weightedSum += weightDf.loc[col, 'scoreWeight']
            denominator += weightDf.loc[col, 'scoreWeight']
        except KeyError:
            print(f"KeyError: {col} not found in weightDf")
            continue

    cutoff = cutoff / len(notNA)
    weightedCutoff = weightedCutoff / denominator
    weightedScore = round((weightedSum / denominator * 100), 2)
    print(f'Cutoff: {cutoff}, Weighted Cutoff: {weightedCutoff}, Weighted Sum: {weightedSum}, Denominator: {denominator}')
    # CS TS ES PS  all should become 0 if no value is present
    row[colTS] = row[colTS] if pd.notna(row[colTS]) else 0
    row[colES] = row[colES] if pd.notna(row[colES]) else 0
    row[colCS] = row[colCS] if pd.notna(row[colCS]) else 0
    row[colPS] = row[colPS] if pd.notna(row[colPS]) else 0

    totalScore = weightMC * weightedScore + (weightTS * row[colTS]/4 + weightES * row[colES]/4 + weightPS * row[colPS]/2 + weightCS * row.get(colCS,0)/2)*100
    df.at[i, 'Cutoff'] = round(cutoff, 2)
    df.at[i, 'Weighted Cutoff'] = round(weightedCutoff, 2)
    df.at[i, 'Weighted Score'] = weightedScore
    df.at[i, 'Total Score'] = round(totalScore, 2)
    

MC1     Yes
MC2      No
MC3      No
MC4     Yes
MC5      No
MC6      No
MC7     Yes
MC8     Yes
MC9     Yes
MC12     No
MC13     No
MC14    Yes
MC15     No
MC16     No
MC17     No
MC18     No
MC19    Yes
MC20     No
MC21    Yes
MC22     No
MC23    Yes
MC24     No
MC25    Yes
MC26    Yes
Name: 0, dtype: object

Cutoff: 47.291666666666664, Weighted Cutoff: 47.85, Weighted Sum: 45, Denominator: 100


MC1     Yes
MC2      No
MC3     Yes
MC4     Yes
MC5      No
MC6      No
MC7      No
MC8     Yes
MC9     Yes
MC12    Yes
MC13     No
MC14     No
MC15    Yes
MC16     No
MC17     No
MC18     No
MC19     No
MC20     No
MC21    Yes
MC22     No
MC23     No
MC24    Yes
MC25    Yes
MC26    Yes
Name: 1, dtype: object

Cutoff: 47.291666666666664, Weighted Cutoff: 47.85, Weighted Sum: 49, Denominator: 100


MC1     Yes
MC2      No
MC3     Yes
MC4     Yes
MC5     Yes
MC6     Yes
MC7     Yes
MC8     Yes
MC9     Yes
MC12     No
MC13     No
MC14     No
MC15    Yes
MC16     No
MC17     No
MC18     No
MC19     No
MC20     No
MC21    Yes
MC22     No
MC23     No
MC24    Yes
MC25    Yes
MC26    Yes
Name: 2, dtype: object

...

Cutoff: 47.291666666666664, Weighted Cutoff: 47.85, Weighted Sum: 47, Denominator: 100


MC1     Yes
MC2     Yes
MC3     Yes
MC4     Yes
MC5      No
MC6     Yes
MC7      No
MC8     Yes
MC9     Yes
MC12     No
MC13     No
MC14     No
MC15    Yes
MC16     No
MC17     No
MC18    Yes
MC19     No
MC20     No
MC21    Yes
MC22     No
MC23    Yes
MC24    Yes
MC25    Yes
MC26    Yes
Name: 10, dtype: object

Cutoff: 47.291666666666664, Weighted Cutoff: 47.85, Weighted Sum: 60, Denominator: 100


MC1     Yes
MC2      No
MC3     Yes
MC4     Yes
MC5     Yes
MC6     Yes
MC7     Yes
MC8     Yes
MC9     Yes
MC12     No
MC13    Yes
MC14     No
MC15     No
MC16     No
MC17     No
MC18    Yes
MC19     No
MC20     No
MC21    Yes
MC22     No
MC23    Yes
MC24    Yes
MC25    Yes
MC26    Yes
Name: 11, dtype: object

Cutoff: 47.291666666666664, Weighted Cutoff: 47.85, Weighted Sum: 63, Denominator: 100


In [64]:
df[mcCols] = df[mcCols].replace({'Yes': 1, 'No': 0})
display(df.head())

Assessment ID  Student Name  Student ID                 Date Cohort  \
0            990     Kelly Liu     1081400  2025-07-18T00:00:00   DDS2   
1            925     Kelly Liu     1081400  2025-07-18T00:00:00   DDS2   
2            926  Yueyang Zhou     1541150  2025-07-18T00:00:00   DDS2   
3            904   Karn Chohan     1402793  2025-07-18T00:00:00   DDS2   
4            905  Zohra Asghar     1402796  2025-07-18T00:00:00   DDS2   

     Subject        Type  Completed  MC1  MC2  MC3  MC4  MC5  MC6  MC7  MC8  \
0  DENT90146  Simulation       True    1    0    0    1    0    0    1    1   
1  DENT90146  Simulation       True    1    0    1    1    0    0    0    1   
2  DENT90146  Simulation       True    1    0    1    1    1    1    1    1   
3  DENT90146  Simulation       True    1    0    1    1    0    0    0    1   
4  DENT90146  Simulation       True    1    0    1    1    0    1    0    1   

   MC9 MC10 MC11  MC12  MC13  MC14  MC15  MC16  MC17  MC18  MC19  MC20  MC21  \
0    1   NA   NA     0     0     1     0     0     0     0     1     0     1   
1    1   NA   NA     1     0     0     1     0     0     0     0     0     1   
2    1   NA   NA     0     0     0     1     0     0     0     0     0     1   
3    1   NA   NA     0     0     0     1     0     0     0     0     0     1   
4    1   NA   NA     1     0     0     1     0     0     0     0     1     1   

   MC22  MC23  MC24  MC25  MC26 PEC_MC1 PEC_MC2  TS  CS  PS  ES  \
0     0     1     0     1     1     Yes     Yes   3   2   2   2   
1     0     0     1     1     1     Yes     Yes   3   2   2   2   
2     0     0     1     1     1     Yes     Yes   3   2   2   2   
3     0     1     1     1     1     Yes     Yes   3   2   2   1   
4     0     1     1     1     1     Yes     Yes   3   2   2   2   

                                   Assessor Feedback  Cutoff  Weighted Cutoff  \
0  12 large porosity in mesial near margin, open ...   47.29            47.85   
1  14 mild divergence of palatal wall. Caries occ...   47.29            47.85   
2  14 caries removal good but minor palatal diver...   47.29            47.85   
3  14 caries removal good but slight divergent pa...   47.29            47.85   
4  14 caries management ok but divergent palatal ...   47.29            47.85   

   Weighted Score  Total Score  
0            45.0        49.25  
1            49.0        52.35  
2            53.0        55.45  
3            49.0        48.60  
4            60.0        60.88

In [65]:
df.to_excel(os.path.join(folder, f"DDS2 resit 18-07-2025 scores.xlsx"), index=False)